In [1]:
import math as m
import numpy as np
import matplotlib.pyplot as plt
from scipy import integrate
from scipy import interpolate

### Alternative to the standar method for solving TOV, inspired on the newtonian case worked by astrophysicists.

## System of Equations

The equations of structure of an compact object with spherical symmetry (neutron stars in our case) is given by (in units where $c=G=1$):

$$ P=P(\rho), $$
$$ \frac{dm}{dr}=4\pi \rho r^2 , $$
$$ \frac{dP}{dr}=-(\rho+P)\frac{m+4\pi r^3 P}{r(r-2m)} , $$

Keeping the same nondimensionalization:
$$r=b\bar{r} \quad ; \quad \rho=\Sigma \bar{\rho} \quad ; \quad m=m_c\bar{m} \quad ; \quad  P=P_c \bar{P}$$

$$ \Sigma=\frac{m_{n}^{4}c^{3}}{8 \pi^2 \hbar^3}\quad;\quad b=\frac{c}{\sqrt{\Sigma G}}\quad, \quad m= \frac{b c^2}{G} \bar{m} \quad; \quad P= \Sigma c^2 \bar{P},$$

we have the system of equations

$$ \bar{P}=\bar{P}(\bar{\rho}), $$
$$ \frac{d\bar{m}}{\bar{dr}}=4\pi \bar{\rho} \bar{r}^2 , $$
$$ \frac{d\bar{P}}{d\bar{r}}=-\left(\bar{\rho}+\bar{P}\right)\frac{\bar{m}+4\pi \bar{r}^3 \bar{P}}{\bar{r}(\bar{r}-2\bar{m})} . $$

We want to change the independent variable to $m$, we find the reciprocal to the second equation:

$$\frac{d\bar{r}}{d\bar{m}}=\frac{1}{4\pi\bar{\rho}\bar{r}^2}\quad \longrightarrow \quad \frac{1}{d\bar{r}}=\frac{4\pi \bar{\rho} \bar{r}^2}{dm},$$

and replacing it in the third we have the system in the form:

$$ \bar{P}=\bar{P}{\left(\bar{\rho}\right)}  \quad  ; \quad \bar{\rho}=\bar{\rho}{\left(\bar{P}\right)} $$

$$ \frac{d\bar{P}}{d\bar{m}} = -\frac{\left(\bar{\rho}+\bar{P}\right)}{4\pi\bar{r}^3\bar{\rho}} \frac{\bar{m}+4\pi\bar{P}\bar{r}^3}{(\bar{r}-2\bar{m})} $$

$$ \frac{d\bar{r}}{d\bar{m}}=\frac{1}{4\pi\bar{\rho}\bar{r}^2} $$

## Solving the system

In [2]:
import Physical_Const as phys
h=phys.h 
c=phys.c
G=phys.G
Msun=phys.Msun
mn=phys.mn # Neutron mass


Sigma=mn**4.0*c**3.0/(8.0*np.pi**2*(h/(2.0*np.pi))**3.0)
br=c/np.sqrt(Sigma*G) 
Mdim=(br*c**2.0/G)/Msun # So that m is measured in Solar masses

In [3]:
Sigma

2280831545249651.0

In [4]:
Mdim

16.464490729612635

In [5]:
br

2430587.054706729

In [6]:
rhoEoS,PEoS=np.loadtxt('EOSFull_NL3_BPS02.dat',usecols=(0,1),unpack=True) 

# Interpolating P
EoS_NL302=interpolate.interp1d(rhoEoS/Sigma,PEoS/(c**2.0*Sigma)) 


# Interpolating Rho
EoS_NL3=interpolate.interp1d(PEoS/(c**2.0*Sigma),rhoEoS/Sigma)

def rho_EoS(x):
    rhorho=interpolate.interp1d(PEoS/(c**2.0*Sigma),rhoEoS/Sigma)
    return rhorho(x)

In [14]:
def TOV(m,y):
    rns = y[0]
    pns = y[1]
    print(pns,rho_EoS(pns))
    dpdm=-((pns+rho_EoS(pns))*(m+4.0*np.pi*pns*(rns**3.0)))/(4.0*np.pi*rho_EoS(pns)*(rns**3.0)*(rns-2.0*m))
    drdm=1.0/(4.0*np.pi*(rns**2.0)*rho_EoS(pns))
    return [drdm,dpdm]

# Stellar structure

# Mass-radius relation

In [19]:
def StaticSeqMR(y0,m0,dm):
    Static=integrate.ode(TOV).set_integrator('dopri5',atol=1e-9) # Dopri (Dorman-Prince method) is a R-K method of order (4)5
    Static.set_initial_value(y0,m0)
    #global mms,pexs,rs
    #mms=[]; pexs=[];rs=[]
    #rs.append(y0[0]); pexs.append(y0[1]); mms.append(m0)
    while Static.successful() and Static.y[1] > 1e-9:
        print(Static.y[1],rho_EoS(Static.y[1]),dm,'w')
        Static.integrate(Static.t+dm)
    rstar=Static.y[0]
    mstar=Static.t 
    return [mstar*Mdim,rstar*br*1e-5] 
    # Returns mass of the star in solar masses and radius of the star in km

In [21]:
#Initial values
dm1=1e-9# Step size
m01=0 # Initial point
mf1=2 # Final point
rhoc=np.arange(14.1,15.5,0.05)
xc=EoS_NL302((10.0**rhoc)/Sigma) 

In [12]:


MM=[];RR=[]

for xcc in xc:
    MR=StaticSeqMR([1e-7,xcc],m01,dm1)
    print(MR)
    RR=RR+[MR[1]]
    MM=MM+[MR[0]]

0.0005121992539266007
0.0005121992539264793
0.0005121992539241715
0.0005121992539256858
0.0005121992539146208
0.0005121992538904757
0.0005121992538917943
0.0005121992539254699
0.000512199253925765
0.0005121992539262833
0.0005121992539224047
0.0005121992539139821
0.0005121992539144554
0.0005121992539261954
0.0005121992539262572
0.0005121992539264678
0.0005121992539247717
0.0005121992539211398
0.0005121992539213614
0.0005121992539264147
0.0005121992539264363
0.0005121992539265349
0.0005121992539255084
0.0005121992539234008
0.0005121992539235631
0.0005121992539264786
0.000512199253926511
0.0005121992539265626
0.0005121992539255374
0.0005121992539235767
0.000512199253923786
0.0005121992539264694
0.0005121992539265453
0.0005121992539265748
0.0005121992539251599
0.0005121992539225813
0.0005121992539229135
0.0005121992539264147
0.0005121992539265621
0.0005121992539265799
0.0005121992539246511
0.0005121992539212029
0.0005121992539216793
0.0005121992539263454
0.0005121992539265701
0.00051219925

ValueError: A value in x_new is below the interpolation range.

In [22]:
StaticSeqMR([1e-7,xc[2]],0,1e-9)

0.0010024958942236061 0.06948751632982353 1e-06 w
0.0010024958942236061 0.06948751632982353
0.0010024958942231616 0.06948751632981268
0.001002495894214714 0.06948751632960645
0.0010024958942202616 0.06948751632974189
0.0010024958941798785 0.06948751632875605
0.001002495894091687 0.06948751632660312
0.001002495894096481 0.06948751632672015
0.0010024958942194953 0.06948751632972318
0.001002495894220737 0.06948751632975349
0.0010024958942225202 0.06948751632979702
0.0010024958942093185 0.06948751632947474
0.0010024958941805878 0.06948751632877337
0.0010024958941821814 0.06948751632881227
0.0010024958942222394 0.06948751632979017
0.0010024958942224894 0.06948751632979627
0.0010024958942231774 0.06948751632981306
0.0010024958942178516 0.06948751632968304
0.0010024958942063645 0.06948751632940263
0.0010024958942070354 0.069487516329419
0.0010024958942230337 0.06948751632980955
0.0010024958942230961 0.06948751632981108
0.001002495894223405 0.06948751632981862
0.001002495894220668 0.0694875163

KeyboardInterrupt: 

In [ ]:
rho_EoS(-1)